# Blocking with Word2Vec

In [55]:
from gensim.models import Word2Vec
from gensim.utils import simple_preprocess
from sklearn.cluster import KMeans
import numpy as np
import pandas as pd
import os
import gensim.downloader as api
from sklearn.metrics import silhouette_score
import csv

In [56]:
import os

num_threads = os.cpu_count()
print("Numero di thread disponibili:", num_threads)

Numero di thread disponibili: 8


In [57]:
schema_mediato = pd.read_csv("./../../datasets/MediatedSchemaSemicolon.csv",sep=";")

In [58]:
schema_mediato

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  
0                Cybersecurity           2015  
1                      Fintech           2010  
2                       Health           2015  
3      Artificial intelligence           2017  
4        Auto & transportation           2013  
...                        ...            ...  
81701                      NaN            NaN  
81702                      NaN            NaN  
81703                      NaN            NaN  
81704                      NaN            NaN  
81705                      NaN            NaN  

[81706 rows x 6 columns]

In [59]:
records = []

In [60]:
for i in range(0,len(schema_mediato)):
    record = schema_mediato.iloc[i].dropna()
    records.append(record.tolist())

In [61]:
records

[['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'],
 ['Tipalti', 'United States, San Mateo', '$8.3B', 'Fintech', '2010'],
 ['Tempus', 'United States, Chicago', '$8.1B', 'Health', '2015'],
 ['Anduril',
  'United States, Irvine',
  '$8.48B',
  'Artificial intelligence',
  '2017'],
 ['Bolt', 'Estonia, Tallinn', '$8.4B', 'Auto & transportation', '2013'],
 ['ByteDance', 'China, Beijing', '$140B', 'Artificial intelligence', '2012'],
 ['Niantic',
  'United States, San Francisco',
  '$9B',
  'Mobile & telecommunications',
  '2015'],
 ['OYO Rooms', 'India, Gurugram', '$9B', 'Travel', '2012'],
 ['Kavak',
  'Mexico, Lerma de Villada',
  '$8.7B',
  'E-commerce & direct-to-consumer',
  '2014'],
 ['Personio',
  'Germany, Munich',
  '$8.5B',
  'Internet software & services',
  '2015'],
 ['Klaviyo',
  'United States, Boston',
  '$9.2B',
  'Internet software & services',
  '2012'],
 ['Rapyd', 'United Kingdom, London', '$8.75B', 'Fintech', '2016'],
 ['Nuro',
  'United States, Mou

In [62]:
model = Word2Vec(sentences=records, vector_size=256, window=5, min_count=1, workers=4)

In [9]:
def calculate_vector(record):
    # Inizializza un vettore vuoto
    record_vector = np.zeros(model.vector_size)
    # Somma i vettori di embedding di ciascun token nel record
    for token in record:
        record_vector += model.wv[token]
    #Normalizza il vettore risultante
    record_vector /= 256
    return record_vector

In [63]:
records_w2v = []
for i in range(0, len(records)):
    records_w2v.append(calculate_vector(records[i]))

In [64]:
records_w2v

[array([ 4.60290356e-03, -4.90580715e-03, -3.72484954e-03,  3.25925702e-03,
         8.23273955e-03,  5.42287013e-04,  4.20231762e-03,  1.58150524e-04,
        -3.97691335e-03,  5.87935900e-03, -1.83259107e-04, -4.95255306e-03,
         3.36379257e-04, -4.09241197e-03, -4.39841987e-03,  1.14745026e-03,
         3.30054627e-03, -4.25144833e-03, -1.01282195e-02,  1.36440056e-02,
         5.49255714e-03,  4.63672946e-03, -1.54232220e-03, -1.04096609e-02,
        -4.67904838e-03,  3.34616088e-03,  4.15559846e-03, -2.59491268e-03,
         2.41128197e-03, -8.55608371e-03, -1.34962885e-03,  3.30663493e-03,
        -1.33336757e-03, -1.06712342e-03, -2.45253331e-03,  2.23449404e-03,
         6.64557549e-03, -4.73139070e-03, -3.20209725e-03, -3.46089928e-03,
        -4.64872176e-03,  6.05967360e-03, -4.47802058e-03,  3.87936733e-03,
         8.70887061e-03, -1.02636429e-03, -1.33670007e-04,  4.22777076e-04,
        -3.31568676e-03, -1.50404653e-03, -2.01884423e-03,  2.20791523e-03,
         2.3

In [65]:
df = pd.DataFrame(records_w2v)
df

0         1         2         3         4         5         6    \
0      0.004603 -0.004906 -0.003725  0.003259  0.008233  0.000542  0.004202   
1      0.007711 -0.007086 -0.004299  0.004759  0.011391  0.001471  0.005259   
2      0.005802 -0.006039 -0.004756  0.003978  0.010082  0.000830  0.005037   
3      0.004575 -0.004317 -0.002827  0.002979  0.007038  0.000674  0.003431   
4      0.004746 -0.004725 -0.002860  0.003308  0.007499  0.000522  0.003803   
...         ...       ...       ...       ...       ...       ...       ...   
81701  0.000328 -0.000317  0.000013  0.000182  0.000344  0.000046  0.000161   
81702  0.000383 -0.000317 -0.000043  0.000215  0.000400  0.000116  0.000171   
81703  0.000999 -0.000826 -0.000139  0.000605  0.001130  0.000115  0.000437   
81704  0.001140 -0.000937 -0.000091  0.000774  0.001313  0.000150  0.000541   
81705  0.000322 -0.000271 -0.000082  0.000232  0.000441  0.000086  0.000158   

            7         8         9    ...       246       247       248  \
0      0.000158 -0.003977  0.005879  ...  0.000308  0.004036  0.003586   
1      0.000606 -0.004571  0.006337  ...  0.002152  0.005732  0.004496   
2      0.000129 -0.004983  0.007318  ...  0.000137  0.004929  0.004550   
3      0.000278 -0.002859  0.004060  ...  0.001149  0.003390  0.002883   
4      0.000328 -0.003177  0.004711  ...  0.000877  0.003733  0.003076   
...         ...       ...       ...  ...       ...       ...       ...   
81701  0.000088 -0.000074  0.000063  ...  0.000302  0.000190  0.000131   
81702  0.000119 -0.000008  0.000136  ...  0.000286  0.000252  0.000032   
81703  0.000194 -0.000065  0.000074  ...  0.000703  0.000607  0.000270   
81704  0.000185 -0.000167  0.000168  ...  0.000843  0.000712  0.000264   
81705  0.000126 -0.000080 -0.000029  ...  0.000252  0.000220  0.000111   

            249       250       251       252       253       254       255  
0     -0.004543 -0.005790 -0.000637 -0.006809  0.005716 -0.007082  0.001121  
1     -0.006130 -0.007402 -0.001138 -0.008554  0.007105 -0.009151  0.001592  
2     -0.005735 -0.007335 -0.000796 -0.008626  0.007256 -0.008661  0.001460  
3     -0.003761 -0.004624 -0.000545 -0.005427  0.004511 -0.005551  0.001028  
4     -0.003969 -0.005107 -0.000468 -0.005886  0.004766 -0.006247  0.000882  
...         ...       ...       ...       ...       ...       ...       ...  
81701 -0.000186 -0.000199 -0.000066 -0.000191  0.000131 -0.000218  0.000103  
81702 -0.000145 -0.000200 -0.000042 -0.000146  0.000181 -0.000268  0.000088  
81703 -0.000355 -0.000524 -0.000166 -0.000492  0.000309 -0.000746  0.000157  
81704 -0.000553 -0.000555 -0.000157 -0.000556  0.000357 -0.000858  0.000188  
81705 -0.000131 -0.000155 -0.000065 -0.000212  0.000212 -0.000176  0.000064  

[81706 rows x 256 columns]

## K Means

In [66]:
kmeans = KMeans(n_clusters=2167, random_state=0).fit(df)

/Users/alessandropesare/anaconda3/envs/FinalProjectIDD3_8/lib/python3.8/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


In [67]:
len(kmeans.labels_)

81706

In [69]:
kmeans.labels_

array([ 110,  198, 1504, ..., 1018, 1843,    0], dtype=int32)

In [73]:
schema_mediato['block'] = kmeans.labels_

In [71]:
schema_mediato

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  cluster  
0                Cybersecurity           2015      110  
1                      Fintech           2010      198  
2                       Health           2015     1504  
3      Artificial intelligence           2017      480  
4        Auto & transportation           2013      659  
...                        ...            ...      ...  
81701                      NaN            NaN     1066  
81702                      NaN            NaN        0  
81703                      NaN            NaN     1018  
81704                      NaN            NaN     1843  
81705                      NaN            NaN        0  

[81706 rows x 7 columns]

In [74]:
schema_mediato.to_csv("SchemaMediatoConCluster.csv")

In [68]:
silhouette_score(df,kmeans.labels_)

0.2472871892915824

In [39]:
from itertools import islice

In [40]:

#Esegui il blocking basato sui cluster ottenuti
blocks = {}  # Dizionario che mappa il cluster al suo insieme di record
for i, label in enumerate(kmeans.labels_):
    if label not in blocks:
        blocks[label] = []
    blocks[label].append(records[i])

print("Blocchi ottenuti:")
print(len(blocks))
# Stampare i primi 100 elementi del dizionario
for key, value in islice(blocks.items(), 100):
    print(key, value)

Blocchi ottenuti:
800
403 [['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'], ['Nuro', 'United States, Mountain View', '$8.6B', 'Auto & transportation', '2016'], ['Lalamove', 'Hong Kong, Cheung Sha Wan', '$10B', 'Supply chain, logistics, & delivery', '2013'], ['Leap Motor', 'China, Hangzhou', '$1.01B', 'Auto & transportation', '2015'], ['Rivigo', 'India, Gurgaon', '$1.07B', 'Supply chain, logistics, & delivery', '2014'], ['LEAD School', 'India, Andheri', '$1.1B', 'Edtech', '2012'], ['Flexe', 'United States, Seattle', ' $1B', 'Supply chain, logistics, & delivery', '2013'], ['TravelPerk', 'Spain, Barcelona', '$1.3B', 'Travel', '2015'], ['Tongdun Technology', 'China, Hangzhou', '$1.32B', 'Cybersecurity', '2013'], ['Degreed', 'United States, Pleasanton', '$1.4B', 'Edtech', '2012'], ['Fresh Life Style Supply Chain Management', 'China, Chengdu', ' $1.57 B', 'Supply chain, logistics, & delivery', '2016'], ['Ximalaya FM', 'China, Shanghai', '$1.52B', 'Mobile & telecommu

In [44]:
blocks[403]

[['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'],
 ['Nuro',
  'United States, Mountain View',
  '$8.6B',
  'Auto & transportation',
  '2016'],
 ['Lalamove',
  'Hong Kong, Cheung Sha Wan',
  '$10B',
  'Supply chain, logistics, & delivery',
  '2013'],
 ['Leap Motor', 'China, Hangzhou', '$1.01B', 'Auto & transportation', '2015'],
 ['Rivigo',
  'India, Gurgaon',
  '$1.07B',
  'Supply chain, logistics, & delivery',
  '2014'],
 ['LEAD School', 'India, Andheri', '$1.1B', 'Edtech', '2012'],
 ['Flexe',
  'United States, Seattle',
  ' $1B',
  'Supply chain, logistics, & delivery',
  '2013'],
 ['TravelPerk', 'Spain, Barcelona', '$1.3B', 'Travel', '2015'],
 ['Tongdun Technology', 'China, Hangzhou', '$1.32B', 'Cybersecurity', '2013'],
 ['Degreed', 'United States, Pleasanton', '$1.4B', 'Edtech', '2012'],
 ['Fresh Life Style Supply Chain Management',
  'China, Chengdu',
  ' $1.57 B',
  'Supply chain, logistics, & delivery',
  '2016'],
 ['Ximalaya FM',
  'China, Shanghai',
  

## Preparazione per Record Linkage

In [45]:
schema_con_cluster = schema_mediato.copy()
schema_con_cluster['block'] = kmeans.labels_

In [46]:
schema_con_cluster

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  cluster  
0                Cybersecurity           2015      403  
1                      Fintech           2010      610  
2                       Health           2015      687  
3      Artificial intelligence           2017      372  
4        Auto & transportation           2013      372  
...                        ...            ...      ...  
81701                      NaN            NaN      328  
81702                      NaN            NaN      328  
81703                      NaN            NaN      678  
81704                      NaN            NaN      678  
81705                      NaN            NaN        8  

[81706 rows x 7 columns]

In [47]:
schema_con_cluster.to_csv("SchemaMediatoConCluster.csv")

## Esempio per un solo cluster

In [23]:
cluster5 = schema_con_cluster[schema_con_cluster['cluster'] == 5]
cluster5

name  \
10123                       ValueLabs   
10172                      Tata Elxsi   
10331      Sysnet Global Technologies   
10592  Barclays Global Service Centre   
10843  SoftAge Information Technology   
11220    PrimEra Medical Technologies   
11322     National Informatics Centre   
11344                       Suma Soft   
11556                          Sasken   
11568                IIC Technologies   
11811                    SG Analytics   
11962         Ensure Support Services   
12039                          RedBus   
12893              Bharat IT Services   
12896             e-Centric Solutions   
13035           Uneecops Technologies   
13167             Atyati Technologies   
14080              Syscom Corporation   
14095              Syscom Corporation   
14113                 Webkul Software   
14391                    Innovatiview   
14536                     InnovationM   
14681              Tudip Technologies   
14713              Tudip Technologies   
14838                  Aapna Infotech   
16077                       Aptonline   
16336              Northcorp Software   
16817              Kommineni Infotech   
17291   MicroSpark Software Solutions   
17312   MicroSpark Software Solutions   
17826               Kanerika Software   
18082                Vritti Solutions   
18312           Wizertech Informatics   
18325           Wizertech Informatics   
18392             Indovision Services   
18531                IKF Technologies   
18577            QwikCilver Solutions   
18893            Infocus Technologies   
18896        Secure Network Solutions   
18902              AFour Technologies   
19075      Heureux Software Solutions   
19214       Vengai Software Solutions   
19268             Srijan Technologies   
19287             Srijan Technologies   
19372            Ilensys Technologies   

                                       location marketCap sharePrice  \
10123  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
10172     Bangalore/Bengaluru, Karnataka, India       NaN        NaN   
10331                   Delhi/NCR, Delhi, India       NaN        NaN   
10592                               Pune, India       NaN        NaN   
10843          Gurgaon/Gurugram, Haryana, India       NaN        NaN   
11220  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
11322                          New Delhi, India       NaN        NaN   
11344                               Pune, India       NaN        NaN   
11556     Bangalore/Bengaluru, Karnataka, India       NaN        NaN   
11568  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
11811                               Pune, India       NaN        NaN   
11962                Chennai, Tamil Nadu, India       NaN        NaN   
12039                Bangalore,Karnataka, India       NaN        NaN   
12893               Noida, Uttar Pradesh, India       NaN        NaN   
12896                          Hyderabad, India       NaN        NaN   
13035                   Delhi/NCR, Delhi, India       NaN        NaN   
13167                Bangalore,Karnataka, India       NaN        NaN   
14080               Noida, Uttar Pradesh, India       NaN        NaN   
14095               Noida, Uttar Pradesh, India       NaN        NaN   
14113               Noida, Uttar Pradesh, India       NaN        NaN   
14391               Noida, Uttar Pradesh, India       NaN        NaN   
14536               Noida, Uttar Pradesh, India       NaN        NaN   
14681                  Pune, Maharashtra, India       NaN        NaN   
14713                  Pune, Maharashtra, India       NaN        NaN   
14838               Delhi/NCR, New Delhi, India       NaN        NaN   
16077                          Hyderabad, India       NaN        NaN   
16336          Gurgaon/Gurugram, Haryana, India       NaN        NaN   
16817                          Hyderabad, India       NaN        NaN   
17291                          Hyderabad, India       NaN 

In [36]:
result = pd.merge(cluster5, cluster5, on='cluster', suffixes=('_left', '_right'))
result


name_left                             location_left  \
0                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
1                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
2                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
3                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
4                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
...                    ...                                       ...   
2020  Ilensys Technologies                          Hyderabad, India   
2021  Ilensys Technologies                          Hyderabad, India   
2022  Ilensys Technologies                          Hyderabad, India   
2023  Ilensys Technologies                          Hyderabad, India   
2024  Ilensys Technologies                          Hyderabad, India   

     marketCap_left sharePrice_left             category_left  \
0               NaN             NaN  IT Services & Consulting   
1               NaN             NaN  IT Services & Consulting   
2               NaN             NaN  IT Services & Consulting   
3               NaN             NaN  IT Services & Consulting   
4               NaN             NaN  IT Services & Consulting   
...             ...             ...                       ...   
2020            NaN             NaN  IT Services & Consulting   
2021            NaN             NaN  IT Services & Consulting   
2022            NaN             NaN  IT Services & Consulting   
2023            NaN             NaN  IT Services & Consulting   
2024            NaN             NaN  IT Services & Consulting   

     foundationYear_left  cluster                      name_right  \
0                  1997         5                       ValueLabs   
1                  1997         5                      Tata Elxsi   
2                  1997         5      Sysnet Global Technologies   
3                  1997         5  Barclays Global Service Centre   
4                  1997         5  SoftAge Information Technology   
...                  ...      ...                             ...   
2020               2009         5      Heureux Software Solutions   
2021               2009         5       Vengai Software Solutions   
2022               2009         5             Srijan Technologies   
2023               2009         5             Srijan Technologies   
2024               2009         5            Ilensys Technologies   

                                location_right marketCap_right  \
0     Hyderabad/Secunderabad, Telangana, India             NaN   
1        Bangalore/Bengaluru, Karnataka, India             NaN   
2                      Delhi/NCR, Delhi, India             NaN   
3                                  Pune, India             NaN   
4             Gurgaon/Gurugram, Haryana, India             NaN   
...                                        ...             ...   
2020                   Delhi/NCR, Delhi, India             NaN   
2021                          Hyderabad, India             NaN   
2022                   Delhi/NCR, Delhi, India             NaN   
2023                   Delhi/NCR, Delhi, India             NaN   
2024                          Hyderabad, India             NaN   

     sharePrice_right            category_right foundationYear_right  
0                 NaN  IT Services & Consulting                1997   
1                 NaN  IT Services & Consulting                1989   
2                 NaN  IT Services & Consulting                1999   
3                 NaN  IT Services & Consulting                2007   
4                 NaN  IT Services & Consulting                1994   
...               ...                       ...                  ...  
2020              NaN  IT Services & Consulting                2015   
2021              NaN  IT Services & Consulting                2010   
2022              NaN  IT Services & Consulting                2002   
2023              NaN  IT Services & Co